In [ ]:
import requests
import pandas as pd
import geopandas as gpd

r = requests.get("https://zenodo.org/api/records/7763642")
version = r.json()["metadata"]["version"]
files = {i["key"]:i["links"]["self"] for i in r.json()["files"]}
doms = gpd.read_file(files[f'SvalboxDMDb_v{version.replace(".","-")}.geojson'])
parameters = pd.read_json(files[f'SvalboxDMDb_v{version.replace(".","-")}_parameters.json'])

print(f'The SvalboxDMDb_v{version} contains {len(doms)} models and covers {round(doms.proc_coverage_area.sum(),3)} km2.')

In [ ]:
import cartopy.crs as ccrs
import cartopy.io.shapereader as shpreader
import shapely.geometry as sgeom
import geopandas as gpd
from datetime import datetime as dt
import seaborn as sns
from matplotlib.colors import LogNorm, Normalize, SymLogNorm
import matplotlib.pyplot as plt
from cmcrameri import cm
import json

# Figure 4, 5 and 6

In [ ]:
# Preparing of the data prior to plotting

doms["acq_camera_model_type"] = 0
doms.loc[doms[doms.acq_camera_model.str.contains("Hasselblad|DJI")].index,"acq_camera_model_type"] = "UAV"
doms.loc[doms[doms.acq_camera_model.str.contains("NIKON")].index,"acq_camera_model_type"] = "Handheld"
doms.loc[doms[doms.acq_camera_model.str.contains("iPhone")].index,"acq_camera_model_type"] = "Phone"
doms.loc[doms[doms.acq_camera_model.str.contains(";")].index,"acq_camera_model_type"] = "Combination"

doms["acq_camera_model_type"] = doms["acq_camera_model_type"].astype("category")
doms["acq_camera_model_type"] = doms["acq_camera_model_type"].cat.set_categories(["Phone", "Handheld", "UAV", "Combination"], ordered=True)

doms.acq_camera_model = doms.acq_camera_model.replace({
    "Hasselblad L1D-20c":"Mavic 2 Pro",
    "DJI FC300X":"Phantom 3",
    "DJI FC2103":"Mavic Air",
    "DJI FC220":"Mavic Pro",
    "DJI FC3170":"Mavic Air 2",
})

for k,v in {
    "Hasselblad L1D-20c":"Mavic 2 Pro",
    "DJI FC300X":"Phantom 3",
    "DJI FC2103":"Mavic Air",
    "DJI FC220":"Mavic Pro",
    "DJI FC3170":"Mavic Air 2"
}.items():
    doms.acq_camera_model = doms.acq_camera_model.str.replace(k,v)


doms.sort_values(by=["acq_camera_model_type", "acq_camera_model"],inplace=True)

## Figure 4

The Svalbard lands/provinces have been digitized from the descriptions
provided by the Norwegian Polar Institute, and may be slightly off.

An example is found below for Nordenskioldland:
https://placenames.npolar.no/Nordenski%C3%B6ld_Land/Svalbard/276f367f-7202-5c1d-a3b0-4e493c0b4168


In [ ]:
lands = gpd.read_file("Svalbard_Lands.gpkg")

In [ ]:
dfsjoin = gpd.sjoin(lands, gpd.GeoDataFrame(doms["acq_date"],geometry=doms.centroid))
dfsjoin["geometry"] = lands["geometry"]
dfsjoin["acq_date"] = pd.to_datetime(dfsjoin.acq_date)
dfsjoin["month"] = dfsjoin.acq_date.dt.month
monthly_counts = dfsjoin.groupby(by=["id","month"]).size()
dfsjoin["count"] = dfsjoin.groupby(by="id").geometry.transform("count")
dfsjoin.drop_duplicates(subset="geometry", inplace=True)
lands = pd.concat([dfsjoin, lands.drop(dfsjoin.index)]).sort_index()
lands = lands.set_index("id")
lands = lands.join(monthly_counts.unstack(1))
lands = lands.rename({x:dt.strptime(str(x), '%m').strftime("%b") for x in monthly_counts.unstack(1).columns}, axis=1)

In [ ]:
fig,ax = plt.subplots(2,4, subplot_kw={"projection":ccrs.UTM(zone=33)}, figsize=(10,5))

for c,i in enumerate(ax.flatten()):
    i.set_axis_off()
    i.set_ylim(8450000,9000000)
    if c == 7: 
        lands.plot(ax=i, column="count", 
               cmap = cm.roma_r,
               vmin=0,
               vmax=60,
               edgecolor="black",
               linewidth=0.75,
               missing_kwds={
            "color": "lightgrey",
            "edgecolor": "red",
            "hatch": "///",
            "label": "Missing values",
            "linewidth": 0.3,
            "alpha":0.38
        },alpha=0.75, zorder=0)
        i.set_title("Total", y=-0.05, pad=-5)
    elif c == 3:
        print("") # colorbar goes here.
        
    elif c > 3:
        lands.plot(ax=i, column=dt.strptime(str(c+3), '%m').strftime("%b"), 
                   cmap = cm.roma_r,
                   vmin=0,
                   vmax=60,
                   edgecolor="black",
                   linewidth=0.75,
                   missing_kwds={
                "color": "lightgrey",
                "edgecolor": "red",
                "hatch": "///",
                "label": "Missing values",
                "linewidth": 0.3,
                "alpha":0.38
            },alpha=0.75, zorder=0)
        i.set_title(dt.strptime(str(c+3), '%m').strftime("%B"), y=-0.05, pad=-5)
    else:
        lands.plot(ax=i, column=dt.strptime(str(c+4), '%m').strftime("%b"), 
                   cmap = cm.roma_r,
                   vmin=0,
                   vmax=60,
                   edgecolor="black",
                   linewidth=0.75,
                   missing_kwds={
                "color": "lightgrey",
                "edgecolor": "red",
                "hatch": "///",
                "label": "Missing values",
                "linewidth": 0.3,
                "alpha":0.38
            },alpha=0.75, zorder=0)
        i.set_title(dt.strptime(str(c+4), '%m').strftime("%B"), y=1.05, pad=0)
        
    
cax = fig.add_axes([0.8, 0.55, 0.015, 0.35])
cbar = fig.colorbar(ax.flatten()[-2].collections[0], cax=cax, extend="max")
cbar.set_label("# of models")

plt.subplots_adjust(left=0.05,
                    bottom=0.05, 
                    right=0.95, 
                    top=0.95, 
                    wspace=0.05, 
                    hspace=0.05)

## Figure 5

In [ ]:
norm = Normalize(0,7)
sm = plt.cm.ScalarMappable(cmap=cm.roma_r, norm=norm)
sm.set_array([])


ax = sns.relplot(
    data=doms, 
    x="proc_ground_resolution", 
    y="proc_camera_total_error", 
    size='proc_flying_altitude', 
    hue='proc_coverage_area', 
    style="acq_camera_model_type",
    #size_norm= (0.1,10),
    aspect=1.3, 
    hue_norm=norm,
    palette = cm.roma_r,
    edgecolor=None,
    #sizes=(25,1000),
).set_axis_labels("Ground resolution (m/pix)","Total camera error (m)")
ax.figure.colorbar(sm, extend="max", label="Footprint (km$^2$)")
ax.set(yscale="log")
ax.set(xscale="log")
ax.set(xlim=(0,0.5), ylim=(0,1000))
ax.legend.remove()
ax.figure.legend(handles=ax.legend.legendHandles[6:11], loc=1, title="   Avg. DOM\ndistance (m)", bbox_to_anchor=(0.24,0.98), facecolor=None, frameon=False)
ax.figure.legend(handles=ax.legend.legendHandles[12:], loc=1, title= "Acquisition\n  method", bbox_to_anchor=(0.4,0.98), facecolor=None, frameon = False)
#plt.savefig(Path(r"../images/footprint-resolution-specs.png"), dpi=450, bbox_inches="tight")

## Figure 6

In [ ]:
norm = Normalize(0,100)
sm = plt.cm.ScalarMappable(cmap=cm.roma_r, norm=norm)
sm.set_array([])

ax = sns.relplot(
    data=doms, 
    x="proc_flying_altitude", 
    y='acq_camera_model', 
    size="proc_coverage_area", 
    hue='proc_camera_total_error', 
    style="acq_camera_model_type",
    size_norm= (0,7),
    aspect=1.61, 
    hue_norm=norm,
    palette = cm.roma_r,
    edgecolor=None
).set_axis_labels("Avg. DOM distance (m)","Camera model")
ax.figure.colorbar(sm, extend="max", label="Total camera error (m)")
ax.legend.remove()
ax.figure.legend(handles=ax.legend.legendHandles[7:11], loc=1, title="Footprint (km$2$)", bbox_to_anchor=(0.695,0.385), facecolor=None, frameon=False)
ax.figure.legend(handles=ax.legend.legendHandles[12:18], loc=1, title="", bbox_to_anchor=(0.575,0.3325), facecolor=None, frameon=False)